In [1]:
import pandas as pd
import numpy as np
from  sklearn.datasets import load_iris
iris = load_iris()

In [2]:
df = pd.DataFrame(data= iris.data, columns= iris.feature_names)

In [3]:
df

sepal length (cm)  sepal width (cm)  petal length (cm)  petal width (cm)
0                  5.1               3.5                1.4               0.2
1                  4.9               3.0                1.4               0.2
2                  4.7               3.2                1.3               0.2
3                  4.6               3.1                1.5               0.2
4                  5.0               3.6                1.4               0.2
..                 ...               ...                ...               ...
145                6.7               3.0                5.2               2.3
146                6.3               2.5                5.0               1.9
147                6.5               3.0                5.2               2.0
148                6.2               3.4                5.4               2.3
149                5.9               3.0                5.1               1.8

[150 rows x 4 columns]

In [4]:
df['target'] = iris.target

In [5]:

set(df.target.tolist())

{0, 1, 2}

In [6]:
df.head()

sepal length (cm)  sepal width (cm)  petal length (cm)  petal width (cm)  \
0                5.1               3.5                1.4               0.2   
1                4.9               3.0                1.4               0.2   
2                4.7               3.2                1.3               0.2   
3                4.6               3.1                1.5               0.2   
4                5.0               3.6                1.4               0.2   

   target  
0       0  
1       0  
2       0  
3       0  
4       0

In [7]:
import numpy as np

def gini_index(groups, classes):
    n_instances = float(sum([len(group) for group in groups]))
    gini = 0.0
    for group in groups:
        print('this is group', group)
        size = float(len(group))
        if size == 0:
            continue
        score = 0.0
        for class_val in classes:
            p = [row[-1] for row in group].count(class_val) / size
            score += p * p
        gini += (1.0 - score) * (size / n_instances)
    return gini

In [8]:
# explanation of gini index
# https://www.saedsayad.com/decision_tree.htm
# https://www.youtube.com/watch?v=7VeUPuFGJHk


In [9]:
def test_split(index, value, dataset):
    left, right = [], []
    for row in dataset:
        if row[index] < value:
            left.append(row)
        else:
            right.append(row)
    return left, right

In [10]:
def get_split(dataset):
    class_values = list(set(row[-1] for row in dataset))
    b_index, b_value, b_score, b_groups = 999, 999, 999, None
    
    # for each feature in dataset
    for index in range(len(dataset[0])-1):
        
        # for each value in the feature
        for row in dataset:

            # split the dataset into two groups based on the value of the feature
            # if  the value of the feature is less than the value of the feature
            # then the row is added to the left group else it is added to the right group
            groups = test_split(index, row[index], dataset)
            gini = gini_index(groups, class_values)
            if gini < b_score:
                b_index, b_value, b_score, b_groups = index, row[index], gini, groups
                
    return {'index':b_index, 'value':b_value, 'groups':b_groups}

# get_split function is used to find the best split point for a dataset. 
# It does this by iterating over each attribute and each value of the attribute, 
# and then splitting the dataset into two groups based on the value of the attribute.
#  It then calculates the Gini index for the split and keeps track of the best split found so far.
#  The function returns a dictionary containing the index of the attribute, the value of the attribute,
#  the groups created by the split, and the Gini index of the split.



In [11]:
def to_terminal(group):
    outcomes = [row[-1] for row in group]
    return max(set(outcomes), key=outcomes.count)

def split(node, max_depth, min_size, depth):
    left, right = node['groups']
    del(node['groups'])
    
    if not left or not right:
        node['left'] = node['right'] = to_terminal(left + right)
        return
    
    if depth >= max_depth:
        node['left'], node['right'] = to_terminal(left), to_terminal(right)
        return
    
    if len(left) <= min_size:
        node['left'] = to_terminal(left)
    else:
        node['left'] = get_split(left)
        split(node['left'], max_depth, min_size, depth+1)
    
    if len(right) <= min_size:
        node['right'] = to_terminal(right)
    else:
        node['right'] = get_split(right)
        split(node['right'], max_depth, min_size, depth+1)

def build_tree(train, max_depth, min_size):
    root = get_split(train)
    split(root, max_depth, min_size, 1)
    return root


In [12]:
def predict(node, row):
    if row[node['index']] < node['value']:
        if isinstance(node['left'], dict):
            return predict(node['left'], row)
        else:
            return node['left']
    else:
        if isinstance(node['right'], dict):
            return predict(node['right'], row)
        else:
            return node['right']


In [13]:
# Convert dataframe to list for simplicity
dataset = df.values.tolist()

# Build the decision tree
tree = build_tree(dataset, max_depth=3, min_size=1)


this is group [[4.9, 3.0, 1.4, 0.2, 0.0], [4.7, 3.2, 1.3, 0.2, 0.0], [4.6, 3.1, 1.5, 0.2, 0.0], [5.0, 3.6, 1.4, 0.2, 0.0], [4.6, 3.4, 1.4, 0.3, 0.0], [5.0, 3.4, 1.5, 0.2, 0.0], [4.4, 2.9, 1.4, 0.2, 0.0], [4.9, 3.1, 1.5, 0.1, 0.0], [4.8, 3.4, 1.6, 0.2, 0.0], [4.8, 3.0, 1.4, 0.1, 0.0], [4.3, 3.0, 1.1, 0.1, 0.0], [4.6, 3.6, 1.0, 0.2, 0.0], [4.8, 3.4, 1.9, 0.2, 0.0], [5.0, 3.0, 1.6, 0.2, 0.0], [5.0, 3.4, 1.6, 0.4, 0.0], [4.7, 3.2, 1.6, 0.2, 0.0], [4.8, 3.1, 1.6, 0.2, 0.0], [4.9, 3.1, 1.5, 0.2, 0.0], [5.0, 3.2, 1.2, 0.2, 0.0], [4.9, 3.6, 1.4, 0.1, 0.0], [4.4, 3.0, 1.3, 0.2, 0.0], [5.0, 3.5, 1.3, 0.3, 0.0], [4.5, 2.3, 1.3, 0.3, 0.0], [4.4, 3.2, 1.3, 0.2, 0.0], [5.0, 3.5, 1.6, 0.6, 0.0], [4.8, 3.0, 1.4, 0.3, 0.0], [4.6, 3.2, 1.4, 0.2, 0.0], [5.0, 3.3, 1.4, 0.2, 0.0], [4.9, 2.4, 3.3, 1.0, 1.0], [5.0, 2.0, 3.5, 1.0, 1.0], [5.0, 2.3, 3.3, 1.0, 1.0], [4.9, 2.5, 4.5, 1.7, 2.0]]
this is group [[5.1, 3.5, 1.4, 0.2, 0.0], [5.4, 3.9, 1.7, 0.4, 0.0], [5.4, 3.7, 1.5, 0.2, 0.0], [5.8, 4.0, 1.2, 0.2, 0.0]

In [14]:
tree

{'index': 2,
 'value': 3.0,
 'left': {'index': 0,
  'value': 5.1,
  'left': {'index': 0, 'value': 4.9, 'left': 0.0, 'right': 0.0},
  'right': {'index': 0, 'value': 5.1, 'left': 0.0, 'right': 0.0}},
 'right': {'index': 3,
  'value': 1.8,
  'left': {'index': 2, 'value': 5.0, 'left': 1.0, 'right': 2.0},
  'right': {'index': 2, 'value': 4.9, 'left': 2.0, 'right': 2.0}}}

In [15]:

# Make predictions
for row in dataset[:60]:
    prediction = predict(tree, row)
    print('Expected=%d, Got=%d' % (row[-1], prediction))


Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=0, Got=0
Expected=1, Got=1
Expected=1, Got=1
Expected=1, Got=1
Expected=1, Got=1
Expected=1, Got=1
Expected=1

<h1> Decision tree for resression problem </h2>

In [ ]:
def mse(groups):
    mse_total = 0.0
    for group in groups:
        if len(group) == 0:
            continue
        actual_values = [row[-1] for row in group]
        mean_value = np.mean(actual_values)
        mse_total += sum((x - mean_value) ** 2 for x in actual_values)
    return mse_total


In [ ]:
def test_split(index, value, dataset):
    left, right = [], []
    for row in dataset:
        if row[index] < value:
            left.append(row)
        else:
            right.append(row)
    return left, right


In [ ]:
def get_split(dataset):
    b_index, b_value, b_score, b_groups = 999, 999, float('inf'), None
    
    for index in range(len(dataset[0])-1):
        for row in dataset:
            groups = test_split(index, row[index], dataset)
            mse_score = mse(groups)
            if mse_score < b_score:
                b_index, b_value, b_score, b_groups = index, row[index], mse_score, groups
                
    return {'index': b_index, 'value': b_value, 'groups': b_groups}


In [ ]:
def to_terminal(group):
    outcomes = [row[-1] for row in group]
    return np.mean(outcomes)

def split(node, max_depth, min_size, depth):
    left, right = node['groups']
    del(node['groups'])
    
    if not left or not right:
        node['left'] = node['right'] = to_terminal(left + right)
        return
    
    if depth >= max_depth:
        node['left'], node['right'] = to_terminal(left), to_terminal(right)
        return
    
    if len(left) <= min_size:
        node['left'] = to_terminal(left)
    else:
        node['left'] = get_split(left)
        split(node['left'], max_depth, min_size, depth+1)
    
    if len(right) <= min_size:
        node['right'] = to_terminal(right)
    else:
        node['right'] = get_split(right)
        split(node['right'], max_depth, min_size, depth+1)

def build_tree(train, max_depth, min_size):
    root = get_split(train)
    split(root, max_depth, min_size, 1)
    return root


In [ ]:
def predict(node, row):
    if row[node['index']] < node['value']:
        if isinstance(node['left'], dict):
            return predict(node['left'], row)
        else:
            return node['left']
    else:
        if isinstance(node['right'], dict):
            return predict(node['right'], row)
        else:
            return node['right']


In [ ]:
import pandas as pd
import numpy as np

# Creating a simple regression dataset
data = {'X1': [2.5, 5.0, 7.5, 10.0, 12.5, 15.0, 17.5, 20.0, 22.5, 25.0],
        'X2': [2.4, 4.9, 7.6, 10.2, 12.4, 15.5, 17.7, 20.2, 22.4, 25.5],
        'y': [5, 10, 15, 20, 25, 30, 35, 40, 45, 50]}

df = pd.DataFrame(data)

# Convert dataframe to list for simplicity
dataset = df.values.tolist()

# Build the regression decision tree
tree = build_tree(dataset, max_depth=3, min_size=1)

# Make predictions
for row in dataset:
    prediction = predict(tree, row)
    print('Expected=%.3f, Got=%.3f' % (row[-1], prediction))


'Hi   there. How are you!'